<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Interruptiegraaf-algemene-beschouwingen-2013" data-toc-modified-id="Interruptiegraaf-algemene-beschouwingen-2013-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Interruptiegraaf algemene beschouwingen 2013</a></span><ul class="toc-item"><li><span><a href="#Stap-1-data-ophalen" data-toc-modified-id="Stap-1-data-ophalen-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Stap 1 data ophalen</a></span></li></ul></li><li><span><a href="#Stap-2:-even-inspecteren" data-toc-modified-id="Stap-2:-even-inspecteren-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Stap 2: even inspecteren</a></span></li><li><span><a href="#Stap-3:-extraheer-het-netwerk" data-toc-modified-id="Stap-3:-extraheer-het-netwerk-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Stap 3: extraheer het netwerk</a></span></li><li><span><a href="#Naar-spreadsheet" data-toc-modified-id="Naar-spreadsheet-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Naar spreadsheet</a></span></li><li><span><a href="#Stap-4-Excel-on-steroids:-pandas" data-toc-modified-id="Stap-4-Excel-on-steroids:-pandas-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Stap 4 Excel on steroids: pandas</a></span><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#Wie-interrumpeert-wie-en-hoe-vaak?" data-toc-modified-id="Wie-interrumpeert-wie-en-hoe-vaak?-5.0.1"><span class="toc-item-num">5.0.1&nbsp;&nbsp;</span>Wie interrumpeert wie en hoe vaak?</a></span></li></ul></li></ul></li><li><span><a href="#Tot-slot:-een-mooi-netwerk" data-toc-modified-id="Tot-slot:-een-mooi-netwerk-6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Tot slot: een mooi netwerk</a></span></li><li><span><a href="#Todo" data-toc-modified-id="Todo-7"><span class="toc-item-num">7&nbsp;&nbsp;</span>Todo</a></span></li><li><span><a href="#Tot-echt-slot:-NLP-op-de-handelingen" data-toc-modified-id="Tot-echt-slot:-NLP-op-de-handelingen-8"><span class="toc-item-num">8&nbsp;&nbsp;</span>Tot echt slot: NLP op de handelingen</a></span></li><li><span><a href="#Exercise" data-toc-modified-id="Exercise-9"><span class="toc-item-num">9&nbsp;&nbsp;</span>Exercise</a></span></li><li><span><a href="#Finding-best-colocations" data-toc-modified-id="Finding-best-colocations-10"><span class="toc-item-num">10&nbsp;&nbsp;</span>Finding best colocations</a></span></li><li><span><a href="#Exercise" data-toc-modified-id="Exercise-11"><span class="toc-item-num">11&nbsp;&nbsp;</span>Exercise</a></span></li></ul></div>

# Interruptiegraaf algemene beschouwingen 2013

Ons doel is iets te maken als  <http://politicalmashup.nl/new/uploads/2010/11/1898466.pdf>.

![](interruptiegraaf.png)
Een handige samenvatting van de interruptiestructuur van een heel debat in de Tweede Kamer.

We laten zien hoe we dat doen in 4 stappen. 
* We gebruiken de XML structuur van de data om makkelijk de gegevens eruit te vissen
* we gebruiken dan `pandas` en `networkx` om de gewenste gegevens snel uit te rekenen en mooi visueel te presenteren.

## Stap 1 data ophalen

* Zoeken met <http://search.politicalmashup.nl/>

* Doordat Wilders moeilijk deed is het debat in tweeen gesplitst en moeten we dus 2 XML files ophalen.
* Bron PDF bestand: <https://zoek.officielebekendmakingen.nl/h-tk-20132014-5-2.pdf>


* <http://resolver.politicalmashup.nl/nl.proc.ob.d.h-tk-20132014-5-2?view=html&q=%22beschouwingen%22#nl.proc.ob>
* <http://resolver.politicalmashup.nl/nl.proc.ob.d.h-tk-20132014-5-4?view=html&q=%22beschouwingen%22#nl.proc.ob.d.h-tk-20132014-5-4.1>

In [ ]:
import requests
from bs4 import BeautifulSoup

f = requests.get('http://resolver.politicalmashup.nl/nl.proc.ob.d.h-tk-20132014-5-4')
f2 = requests.get('http://resolver.politicalmashup.nl/nl.proc.ob.d.h-tk-20132014-5-2')
soup, soup2 = BeautifulSoup(f.text,'lxml'), BeautifulSoup(f2.text,'lxml')


In [ ]:
# pak alle scenes eruit
scenes = soup.findAll('scene')+soup2.findAll('scene')
len(scenes)

# Stap 2: even inspecteren

In [ ]:
a= scenes[0] # pak de eerste scene
a 

In [ ]:
# pak een spreker

a['pm:speaker']

In [ ]:
# Pak alle interruptors van Zijlstra

[s['pm:speaker']  for s in a.findAll('speech')  if s['pm:speaker'] != 'Zijlstra' ]

# Stap 3: extraheer het netwerk

We volgen dit "recept"

 
* Van elke scene
    * pak de spreker X
    * voor elke speech in scene waar spreker is Y en Y$\neq$ X
    * Voeg (X,Y) toe aan interruptielijst  (Y interrumpeert X)
* Tel het aantal keer dat een paartje voorkomt
* Maak er een netwerk van

In [ ]:
interruptielijst=[(a['pm:speaker'],s['pm:speaker'])
    for a in scenes  
        for s in a.findAll('speech') 
                  if s['pm:speaker'] != a['pm:speaker']
                 ]
interruptielijst[:5]

In [ ]:
# Nu gaan we tellen
from collections import  Counter

GewogenInterrupties = Counter(interruptielijst)
GewogenInterrupties.most_common(10)

# Naar spreadsheet

In [ ]:
# even omzetten: van dict naar triples  (a,b,w)

Triples= [(p[0],p[1],GewogenInterrupties[p]) for p in GewogenInterrupties]
Triples[:5]

# Stap 4 Excel on steroids: pandas

* even een intermezzo voor we naar de plaatjes gaan

In [ ]:
import pandas as pd

AB=pd.DataFrame(Triples,columns=['Spreker','Interruptor','Hoe_vaak'])

In [ ]:
AB.head()

In [ ]:
# save naar spreadsheet als je dit wilt
AB.to_csv('ABspreadsheet.csv')
!head ABspreadsheet.csv

### Wie interrumpeert wie en hoe vaak?

* Dit is eigenlijk de tabel met "gewogen in en uit degrees"
* Vervang `sum` door `len` in onderstaand commando en je krijgt de gewone in en out degrees.
    * dus door wie iemand is geinterrumpeerd 
    * en wie iemand geinterrumpeerd heeft
    * de margins geven de in en out degrees (eg, wilders heeft indegree van 11 en outdegree van 2)
    
* **Let op** Rutte en van Miltenburg moeten er eigenlijk nog uit als interruptors

In [ ]:
#  Wie interumpeert wie hoe vaak?
AB.pivot_table(index='Spreker', 
               columns='Interruptor',
               values='Hoe_vaak', 
               aggfunc=sum, 
               margins=True).fillna(0).astype(int)
 
 

# Tot slot: een mooi netwerk

In [ ]:
%matplotlib inline
import networkx as nx

G=nx.DiGraph()

G.add_weighted_edges_from(Triples)

In [ ]:
nx.draw_circular(G, with_labels=True);

In [ ]:
# wrong direction of the arrows! Now it is good

NewTriples=[[t[1],t[0],t[2]] for t in Triples]  # Even omdraaien

G=nx.DiGraph()

G.add_weighted_edges_from(NewTriples)
picture= nx.draw_circular(G, with_labels=True);

# Todo

* color nodes in party colors
* make picture larger
* make lines according to the number of "attacks"

Doel: iets als <http://politicalmashup.nl/new/uploads/2010/11/1898466.pdf>

# Tot echt slot: NLP op de handelingen

* We kijken eens hoe goed en snel de pattern module werkt
* Zie <http://www.clips.ua.ac.be/pages/pattern-en#tree>
* We kuenn hiermee POS tagging, chunking, lemmatization en sentence-splitting doen
* Voor dit lange debat doet ie er 21 seconden over.

### Disclaimer: `pattern` werkt alleen in Python 2.

In [ ]:
from pattern.nl import parsetree


In [ ]:
ScenesDict= {s['pm:speaker']:s.text for s in  scenes}

In [ ]:
% time WildersText= parsetree(ScenesDict['Wilders'],  relations=True, lemmata=True)

In [ ]:
a=WildersText[2]
a.adjectives, a.adjectives[0], a.adjectives[0].string
 

In [ ]:
from pattern.nl import pprint

pprint(WildersText[2])

In [ ]:
# Run on all

%time ScenesDictParsed= {s:parsetree(ScenesDict[s],  relations=True, lemmata=True) for s in ScenesDict}

In [ ]:
# some stats: Nr sentences and Nr of words

NrSentences = sum(len(ScenesDictParsed[s]) for s in ScenesDictParsed )
nrWords= sum(len(sentence.words)   for s in ScenesDictParsed for sentence in ScenesDictParsed[s] )
print NrSentences, nrWords

In [ ]:
# Do the same for all speeches

speeches = soup.findAll('speech')+ soup2.findAll('speech')
len(speeches)

In [ ]:
%time SpeechesParsed= {speech['pm:id']:[speech['pm:speaker'],parsetree(speech.text, relations=True, lemmata=True)] for speech in speeches } 

In [ ]:
len(SpeechesParsed)

In [ ]:
SpeechesParsed.items()[:2]

# Exercise

* For each speaker, extract all adjectives (s)he uses and count them.

In [ ]:
from collections import Counter
from collections import defaultdict
import itertools

def AdjectivesfromSentenceList(L):
    return [ w.string for w in list(itertools.chain(*[sentence.adjectives for sentence in L]))]
   
# test
SpeechesParsed.items()[0][1][1]                
AdjectivesfromSentenceList(SpeechesParsed.items()[0][1][1])                

In [ ]:
AdjectivesPerSpeaker=defaultdict(list)
#Speakers= set(SpeechesParsed[s][0] for s in SpeechesParsed)
for  s in SpeechesParsed:
    AdjectivesPerSpeaker[SpeechesParsed[s][0]] += AdjectivesfromSentenceList(SpeechesParsed[s][1]) 

AdjectivesPerSpeakerCount={speaker:Counter(AdjectivesPerSpeaker[speaker]) for speaker in AdjectivesPerSpeaker}    

In [ ]:
AdjectivesPerSpeakerCount['Wilders'].most_common(20)

In [ ]:
# make one big string of all text in all speeches
souptext=[speech.text for speech in soup.findAll('speech')]
speechtext=' '.join(souptext)
speechtext[:200], len(nltk.tokenize.word_tokenize(speechtext))  # aantal woorden


# Finding best colocations

* We try to use several techniques for finding the most interesting colocations (bigrams and trigrams) in a corpus.
* The techniques do not seem to bring us very far: we mostly find obvious things, although often correct, but rather meaningless

In [ ]:
# Finding best colocations
#http://www.nltk.org/howto/collocations.html explains all quite well


# From http://stackoverflow.com/questions/21128689/how-to-get-pmi-scores-for-trigrams-with-nltk-collocations-python


import nltk
from nltk.collocations import *

#myFile = open("large.txt", 'r').read()

# Make a nltk text out of our speeches
myList = nltk.tokenize.word_tokenize(speechtext)
myCorpus = nltk.Text(myList)


trigram_measures = nltk.collocations.TrigramAssocMeasures()
finder = TrigramCollocationFinder.from_words((myCorpus))

finder.apply_freq_filter(3)
finder.nbest(trigram_measures.pmi, 20) 

In [ ]:
myCorpus.collocations(window_size=3)

In [ ]:
# vindt bigrammen
bigram_measures = nltk.collocations.BigramAssocMeasures()
finder = BigramCollocationFinder.from_words((myCorpus))

finder.apply_freq_filter(3)
bigrams=finder.nbest(bigram_measures.pmi, 200)
bigrams[:10]

In [ ]:
# POS tag de onderdelen van de bigrammen
bistrings= [' '.join(p) for p in bigrams]
parsedbistrings= [ parsetree(p).words for p in bistrings]
len(bistrings),len(parsedbistrings)

In [ ]:
# only take bigrams containing a noun
parsedbistrings_with_noun=[p for p in parsedbistrings if p[0].pos in ['NN', 'NNP'] or p[1].pos in ['NN', 'NNP']]
len(parsedbistrings_with_noun), len(parsedbistrings)
parsedbistrings_with_noun[:5]


In [ ]:
# Print trigram and its pmi-score
def score_ngrams(self, score_fn):
    """Returns a sequence of (ngram, score) pairs ordered from highest to
    lowest score, as determined by the scoring function provided.
    """
    return sorted(self._score_ngrams(score_fn),
                  key=_itemgetter(1), reverse=True)

trigram_measures = nltk.collocations.TrigramAssocMeasures()
finder = TrigramCollocationFinder.from_words(myCorpus)

finder.apply_freq_filter(10)

finder.score_ngrams(trigram_measures.pmi)[:10]
     

In [ ]:
finder.nbest(trigram_measures.pmi, 10) 

# Exercise

* Run bigram/trigram extractor on the parsed input instead of on raw tokenized text

In [ ]:
#step 1
# parse the text: output is a list of words with tokens


from pattern.en import parse

% time parsedspeeches = [parse(s.text) for s in speeches]
tokenized_words_with_pos= ' '.join([s.replace('\n',' ') for s in  parsedspeeches]).split()

#test
len(tokenized_words_with_pos), tokenized_words_with_pos[:50]


In [ ]:
# simplified parse: we only keep the first POS tag

# test example  
# '/'.join(tokenized_words_with_pos[0].split('/')[:2])

simplified_tokenized_words_with_pos= [ '/'.join(w.split('/')[:2]) for w in tokenized_words_with_pos]

In [ ]:
# step 2 find trigrams

finder = TrigramCollocationFinder.from_words(tokenized_words_with_pos)

finder.apply_freq_filter(3)

results=finder.score_ngrams(trigram_measures.pmi)
len(results), results[:10]
   

In [ ]:
finder = BigramCollocationFinder.from_words(tokenized_words_with_pos)

finder.apply_freq_filter(3)

results=finder.score_ngrams(bigram_measures.pmi)
len(results), results[0][0],results[:10]

In [ ]:
# Step 4 Filter out interesting patterns

# test we only want bigrams like (u'complete/JJ/I-NP/O', u'onzin/NN/I-NP/O')

def mathches_pattern(pat,ngram):
    return set(w.split('/')[-1]  for w in pat)  == set(ngram)

OOs= [bi for   bi in results if mathches_pattern(bi[0],[u'B-PNP',u'I-PNP']) ]
OOs[:10]

In [ ]:
# step 5 : compare with the simplified tokens

finder = TrigramCollocationFinder.from_words(simplified_tokenized_words_with_pos)

finder.apply_freq_filter(3)

simple_3results=finder.score_ngrams(trigram_measures.pmi)
# dit werkt nu nite meer
# OOs= [bi for   bi in simple_3results if mathches_pattern(bi[0],u'I-PNP') ]

simple_3results[:10]

# Evaluatie: dit lijkt slechter te werken: de POS tags kloppen eigenlijk vaak helemaal niet